In [2]:
import os
import mne
import numpy as np
import pandas as pd
from scipy.signal import butter, filtfilt, hilbert

C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\venv_eeg\Lib\site-packages\mne\externals\tempita\__init__.py:35: DeprecationWarning: 'cgi' is deprecated and slated for removal in Python 3.13
  import cgi
C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\venv_eeg\Lib\site-packages\mne\datasets\eegbci\eegbci.py:8: UserWarning: pkg_resources is deprecated as an API. See https://setuptools.pypa.io/en/latest/pkg_resources.html. The pkg_resources package is slated for removal as early as 2025-11-30. Refrain from using this package or pin to Setuptools<81.
  import pkg_resources


In [ ]:
processed_folder = r"C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\datasetp\DESTINATION\eeg_preprocesado"
save_folder = r"C:\Users\HP\Documents\PLV_matrices_completas"
os.makedirs(save_folder, exist_ok=True)

# -------------------------------
# Canales malos
# -------------------------------
bad_channels_list = ['F8', 'POz', 'AF4', 'AF8', 'F6', 'FC3']

# -------------------------------
# Función de filtrado
# -------------------------------
def bandpass_filter(data, low, high, sfreq, order=4):
    Wn = [low / (sfreq/2), high / (sfreq/2)]
    b, a = butter(order, Wn, btype='band')
    return filtfilt(b, a, data)

# -------------------------------
# Definir tareas representativas
# -------------------------------
apartados = { 
    "Endomuneca_1": [1,2,3],
    "Endomuneca_2": [4,5,6,7,8],
    "Camara_Embrague": [9,10,11,12,13,14],
    "Control_Aguja": [15,16],
    "Clavado_Aguja": [17,18,19,20,21,22],
    "Energia_Diseccion": [23,24,25,26,27]
}

tareas_representativas = [t[0] for t in apartados.values()]  # [1,4,9,15,17,23]

# -------------------------------
# Diccionario final
# -------------------------------
plv_dict = {}  # plv_dict[tarea][sujeto] = DataFrame 128x128

# -------------------------------
# Procesamiento
# -------------------------------
for subj in os.listdir(processed_folder):
    subj_path = os.path.join(processed_folder, subj)
    if not os.path.isdir(subj_path):
        continue
    
    for tarea in os.listdir(subj_path):
        tarea_path = os.path.join(subj_path, tarea)
        if not os.path.isdir(tarea_path):
            continue
        
        # Extraer número de tarea de la carpeta, ej. "Tarea_1" -> 1
        try:
            tarea_num = int(tarea.split('_')[-1])
        except ValueError:
            print(f"Saltando carpeta {tarea} porque no contiene un número válido")
            continue
        
        if tarea_num not in tareas_representativas:  # solo tareas seleccionadas
            continue
        
        archivos = [f for f in os.listdir(tarea_path) if f.endswith(".fif")]
        if not archivos:
            continue
        
        # Leer primer archivo
        raw = mne.io.read_raw_fif(os.path.join(tarea_path, archivos[0]), preload=True)
        
        # Marcar canales malos
        raw.info['bads'] = [ch for ch in bad_channels_list if ch in raw.ch_names]
        
        # Seleccionar canales buenos
        good_idx = [i for i, ch in enumerate(raw.ch_names) if ch not in raw.info['bads']]
        matriz = raw.get_data(picks=good_idx)
        sfreq = raw.info['sfreq']
        
        # Filtrado 0.5-40 Hz
        matriz_filt = np.zeros_like(matriz)
        for i in range(matriz.shape[0]):
            matriz_filt[i, :] = bandpass_filter(matriz[i, :], 0.5, 40, sfreq)
        
        # Calcular PLV
        analytic_signal = hilbert(matriz_filt, axis=1)
        phases = np.angle(analytic_signal)
        n_channels = matriz.shape[0]
        plv_matrix = np.zeros((n_channels, n_channels))
        
        for i in range(n_channels):
            for j in range(n_channels):
                plv_matrix[i, j] = np.abs(np.mean(np.exp(1j*(phases[i]-phases[j]))))
        
        # Convertir a DataFrame
        ch_names = [raw.ch_names[i] for i in good_idx]
        plv_df = pd.DataFrame(plv_matrix, index=ch_names, columns=ch_names)
        
        # Guardar en diccionario
        if tarea not in plv_dict:
            plv_dict[tarea] = {}
        plv_dict[tarea][subj] = plv_df
        
        # Guardar matriz PLV en Excel
        out_path = os.path.join(save_folder, f"{tarea}_{subj}_PLV.xlsx")
        plv_df.to_excel(out_path, index=True)
        print(f"Guardado: {out_path}")

print("Preprocesamiento y PLV completados para todas las tareas representativas y sujetos.")


Opening raw data file C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\datasetp\DESTINATION\eeg_preprocesado\Sujeto_1\Tarea_1\1_1_1.fif...
Isotrak not found
    Range : 0 ... 18499 =      0.000 ...    36.998 secs
Ready.
Reading 0 ... 18499  =      0.000 ...    36.998 secs...


C:\Users\HP\AppData\Local\Temp\ipykernel_9024\3489457442.py:65: RuntimeWarning: This filename (C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\datasetp\DESTINATION\eeg_preprocesado\Sujeto_1\Tarea_1\1_1_1.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, _meg.fif, _eeg.fif, _ieeg.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz, _meg.fif.gz, _eeg.fif.gz or _ieeg.fif.gz
  raw = mne.io.read_raw_fif(os.path.join(tarea_path, archivos[0]), preload=True)
C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\venv_eeg\Lib\site-packages\mne\io\open.py:160: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  dirpos = int(tag.data)
C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\venv_eeg\Lib\site-packages\mne\io\tag.py:299: Dep

Guardado: C:\Users\HP\Documents\PLV_matrices_completas\Tarea_1_Sujeto_1_PLV.xlsx
Opening raw data file C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\datasetp\DESTINATION\eeg_preprocesado\Sujeto_1\Tarea_15\1_15_1.fif...
Isotrak not found
    Range : 0 ... 48499 =      0.000 ...    96.998 secs
Ready.
Reading 0 ... 48499  =      0.000 ...    96.998 secs...


C:\Users\HP\AppData\Local\Temp\ipykernel_9024\3489457442.py:65: RuntimeWarning: This filename (C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\datasetp\DESTINATION\eeg_preprocesado\Sujeto_1\Tarea_15\1_15_1.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, _meg.fif, _eeg.fif, _ieeg.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz, _meg.fif.gz, _eeg.fif.gz or _ieeg.fif.gz
  raw = mne.io.read_raw_fif(os.path.join(tarea_path, archivos[0]), preload=True)
C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\venv_eeg\Lib\site-packages\mne\io\open.py:160: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  dirpos = int(tag.data)
C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\venv_eeg\Lib\site-packages\mne\io\tag.py:299: D

Guardado: C:\Users\HP\Documents\PLV_matrices_completas\Tarea_15_Sujeto_1_PLV.xlsx
Opening raw data file C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\datasetp\DESTINATION\eeg_preprocesado\Sujeto_1\Tarea_17\1_17_1.fif...
Isotrak not found
    Range : 0 ... 60999 =      0.000 ...   121.998 secs
Ready.
Reading 0 ... 60999  =      0.000 ...   121.998 secs...


...

Guardado: C:\Users\HP\Documents\PLV_matrices_completas\Tarea_9_Sujeto_14_PLV.xlsx
Opening raw data file C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\datasetp\DESTINATION\eeg_preprocesado\Sujeto_15\Tarea_1\15_1_1.fif...
Isotrak not found
    Range : 0 ... 14499 =      0.000 ...    28.998 secs
Ready.
Reading 0 ... 14499  =      0.000 ...    28.998 secs...


C:\Users\HP\AppData\Local\Temp\ipykernel_9024\3489457442.py:65: RuntimeWarning: This filename (C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\datasetp\DESTINATION\eeg_preprocesado\Sujeto_15\Tarea_1\15_1_1.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, _meg.fif, _eeg.fif, _ieeg.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz, _meg.fif.gz, _eeg.fif.gz or _ieeg.fif.gz
  raw = mne.io.read_raw_fif(os.path.join(tarea_path, archivos[0]), preload=True)
C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\venv_eeg\Lib\site-packages\mne\io\open.py:160: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  dirpos = int(tag.data)
C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\venv_eeg\Lib\site-packages\mne\io\tag.py:299: D

Guardado: C:\Users\HP\Documents\PLV_matrices_completas\Tarea_1_Sujeto_15_PLV.xlsx
Opening raw data file C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\datasetp\DESTINATION\eeg_preprocesado\Sujeto_15\Tarea_15\15_15_1.fif...
Isotrak not found
    Range : 0 ... 62999 =      0.000 ...   125.998 secs
Ready.
Reading 0 ... 62999  =      0.000 ...   125.998 secs...


C:\Users\HP\AppData\Local\Temp\ipykernel_9024\3489457442.py:65: RuntimeWarning: This filename (C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\datasetp\DESTINATION\eeg_preprocesado\Sujeto_15\Tarea_15\15_15_1.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, _meg.fif, _eeg.fif, _ieeg.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz, _meg.fif.gz, _eeg.fif.gz or _ieeg.fif.gz
  raw = mne.io.read_raw_fif(os.path.join(tarea_path, archivos[0]), preload=True)
C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\venv_eeg\Lib\site-packages\mne\io\open.py:160: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  dirpos = int(tag.data)
C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\venv_eeg\Lib\site-packages\mne\io\tag.py:299:

Guardado: C:\Users\HP\Documents\PLV_matrices_completas\Tarea_15_Sujeto_15_PLV.xlsx
Opening raw data file C:\Users\HP\Documents\GitHub\Neurociencias-2026-1\S06_proyecto\datasetp\DESTINATION\eeg_preprocesado\Sujeto_15\Tarea_17\15_17_1.fif...
